In [ ]:
from google.colab import drive


In [ ]:
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!rm -rf /content/drive

In [ ]:
drive.flush_and_unmount()


Drive not mounted, so nothing to flush and unmount.


### pre process 
using base line code to process pricipal data 

In [ ]:
!pip install parsivar
!pip install git+https://github.com/RoboEpics/roboepics-client.git

     |████████████████████████████████| 36.2 MB 52 kB/s 
     |████████████████████████████████| 1.5 MB 17.8 MB/s 
  Created wheel for parsivar: filename=parsivar-0.2.3-py3-none-any.whl size=36492971 sha256=4f5cdfb5bd7108cf9c20b9adff54e1dc26627b505dc6a27eee36c8427953ca3a
  Stored in directory: /root/.cache/pip/wheels/ae/67/7a/49cbf08f64d3f76a26eceaf0e481a40e233f05d4356875cbed
  Created wheel for nltk: filename=nltk-3.4.5-py3-none-any.whl size=1449923 sha256=a85071938ec609de045411987c81531cd33f0362d8bc8725e53fbc90b419cd10
  Stored in directory: /root/.cache/pip/wheels/48/8b/7f/473521e0c731c6566d631b281f323842bbda9bd819eb9a3ead
Successfully built parsivar nltk
  Attempting uninstall: nltk
    Found existing installation: nltk 3.2.5
    Uninstalling nltk-3.2.5:
      Successfully uninstalled nltk-3.2.5
  Cloning https://github.com/RoboEpics/roboepics-client.git to /tmp/pip-req-build-it0mqng8
  Running command git clone -q https://github.com/RoboEpics/roboepics-client.git /tmp/pip-req-buil

In [ ]:
from roboepics_client.roboepics_client import RoboEpicsClient

problem_id = 4
problem_enter_id = None  # fill this value with your id

# roboepics_client = RoboEpicsClient(problem_id, problem_enter_id)

In [ ]:
!gdown --id 1uYwzBe8nLhOQ2Q3rCScEXvljLkQqJrHc
!7z x data.7z
!ls


Downloading...
From: https://drive.google.com/uc?id=1uYwzBe8nLhOQ2Q3rCScEXvljLkQqJrHc
To: /content/data.7z
295MB [00:01, 176MB/s]

7-Zip [64] 16.02 : Copyright (c) 1999-2016 Igor Pavlov : 2016-05-21
p7zip Version 16.02 (locale=en_US.UTF-8,Utf16=on,HugeFiles=on,64 bits,4 CPUs Intel(R) Xeon(R) CPU @ 2.20GHz (406F0),ASM,AES-NI)

Scanning the drive for archives:
  0M Scan         1 file, 295109903 bytes (282 MiB)

Extracting archive: data.7z
--
Path = data.7z
Type = 7z
Physical Size = 295109903
Headers Size = 309
Method = LZMA2:24
Solid = +
Blocks = 2

  0%      0% 1 - data/base_products.json                                  1% 1 - data/base_products.json                                  2% 1 - data/base_products.json                                  3% 1 - data/base_products

In [ ]:
from __future__ import unicode_literals

import collections
import gc
import json
import re
import os

import numpy as np
import pandas as pd
import parsivar
from sklearn.feature_extraction.text import TfidfVectorizer
from tqdm import tqdm

In [ ]:
def read_json(path, n_lines_to_read=None):
    """
    read json file line by line iteratively (generator function).
    use this function to read json files when you have memory limitations.
    """

    with open(path) as f:
        for i, line in enumerate(tqdm(f)):
            if n_lines_to_read == i:
                break
            yield json.loads(line)

In [ ]:
parsivar_normalizer = parsivar.Normalizer(statistical_space_correction=True)

char_mappings = {
    "٥": "5",
    "А": "a",
    "В": "b",
    "Е": "e",
    "Н": "h",
    "Р": "P",
    "С": "C",
    "Т": "T",
    "а": "a",
    "г": "r",
    "е": "e",
    "к": "k",
    "м": "m",
    "о": "o",
    "р": "p",
    "ڈ": "د",
    "ڇ": "چ",
    # Persian numbers (will be raplaced by english one)
    "۰": "0",
    "۱": "1",
    "۲": "2",
    "۳": "3",
    "۴": "4",
    "۵": "5",
    "۶": "6",
    "۷": "7",
    "۸": "8",
    "۹": "9",
    ".": ".",
    # Arabic numbers (will be raplaced by english one)
    "٠": "0",
    "١": "1",
    "٢": "2",
    "٣": "3",
    "٤": "4",
    "٥": "5",
    "٦": "6",
    "٧": "7",
    "٨": "8",
    "٩": "9",
    # Special Arabic Characters (will be replaced by persian one)
    "ك": "ک",
    "ى": "ی",
    "ي": "ی",
    "ؤ": "و",
    "ئ": "ی",
    "إ": "ا",
    "أ": "ا",
    "آ": "ا",
    "ة": "ه",
    "ء": "ی",
    # French alphabet (will be raplaced by english one)
    "à": "a",
    "ä": "a",
    "ç": "c",
    "é": "e",
    "è": "e",
    "ê": "e",
    "ë": "e",
    "î": "i",
    "ï": "i",
    "ô": "o",
    "ù": "u",
    "û": "u",
    "ü": "u",
    # Camma (will be replace by dots for floating point numbers)
    ",": ".",
    # And (will be replace by dots for floating point numbers)
    "&": " and ",
    # Vowels (will be removed)
    "ّ": "",  # tashdid
    "َ": "",  # a
    "ِ": "",  # e
    "ُ": "",  # o
    "ـ": "",  # tatvil
    # Spaces
    "‍": "",  # 0x9E -> ZERO WIDTH JOINER
    "‌": " ",  # 0x9D -> ZERO WIDTH NON-JOINER
    # Arabic Presentation Forms-A (will be replaced by persian one)
    "ﭐ": "ا",
    "ﭑ": "ا",
    "ﭖ": "پ",
    "ﭗ": "پ",
    "ﭘ": "پ",
    "ﭙ": "پ",
    "ﭞ": "ت",
    "ﭟ": "ت",
    "ﭠ": "ت",
    "ﭡ": "ت",
    "ﭺ": "چ",
    "ﭻ": "چ",
    "ﭼ": "چ",
    "ﭽ": "چ",
    "ﮊ": "ژ",
    "ﮋ": "ژ",
    "ﮎ": "ک",
    "ﮏ": "ک",
    "ﮐ": "ک",
    "ﮑ": "ک",
    "ﮒ": "گ",
    "ﮓ": "گ",
    "ﮔ": "گ",
    "ﮕ": "گ",
    "ﮤ": "ه",
    "ﮥ": "ه",
    "ﮦ": "ه",
    "ﮪ": "ه",
    "ﮫ": "ه",
    "ﮬ": "ه",
    "ﮭ": "ه",
    "ﮮ": "ی",
    "ﮯ": "ی",
    "ﮰ": "ی",
    "ﮱ": "ی",
    "ﯼ": "ی",
    "ﯽ": "ی",
    "ﯾ": "ی",
    "ﯿ": "ی",
    # Arabic Presentation Forms-B (will be removed)
    "ﹰ": "",
    "ﹱ": "",
    "ﹲ": "",
    "ﹳ": "",
    "ﹴ": "",
    "﹵": "",
    "ﹶ": "",
    "ﹷ": "",
    "ﹸ": "",
    "ﹹ": "",
    "ﹺ": "",
    "ﹻ": "",
    "ﹼ": "",
    "ﹽ": "",
    "ﹾ": "",
    "ﹿ": "",
    # Arabic Presentation Forms-B (will be replaced by persian one)
    "ﺀ": "ی",
    "ﺁ": "ا",
    "ﺂ": "ا",
    "ﺃ": "ا",
    "ﺄ": "ا",
    "ﺅ": "و",
    "ﺆ": "و",
    "ﺇ": "ا",
    "ﺈ": "ا",
    "ﺉ": "ی",
    "ﺊ": "ی",
    "ﺋ": "ی",
    "ﺌ": "ی",
    "ﺍ": "ا",
    "ﺎ": "ا",
    "ﺏ": "ب",
    "ﺐ": "ب",
    "ﺑ": "ب",
    "ﺒ": "ب",
    "ﺓ": "ه",
    "ﺔ": "ه",
    "ﺕ": "ت",
    "ﺖ": "ت",
    "ﺗ": "ت",
    "ﺘ": "ت",
    "ﺙ": "ث",
    "ﺚ": "ث",
    "ﺛ": "ث",
    "ﺜ": "ث",
    "ﺝ": "ج",
    "ﺞ": "ج",
    "ﺟ": "ج",
    "ﺠ": "ج",
    "ﺡ": "ح",
    "ﺢ": "ح",
    "ﺣ": "ح",
    "ﺤ": "ح",
    "ﺥ": "خ",
    "ﺦ": "خ",
    "ﺧ": "خ",
    "ﺨ": "خ",
    "ﺩ": "د",
    "ﺪ": "د",
    "ﺫ": "ذ",
    "ﺬ": "ذ",
    "ﺭ": "ر",
    "ﺮ": "ر",
    "ﺯ": "ز",
    "ﺰ": "ز",
    "ﺱ": "س",
    "ﺲ": "س",
    "ﺳ": "س",
    "ﺴ": "س",
    "ﺵ": "ش",
    "ﺶ": "ش",
    "ﺷ": "ش",
    "ﺸ": "ش",
    "ﺹ": "ص",
    "ﺺ": "ص",
    "ﺻ": "ص",
    "ﺼ": "ص",
    "ﺽ": "ض",
    "ﺾ": "ض",
    "ﺿ": "ض",
    "ﻀ": "ض",
    "ﻁ": "ط",
    "ﻂ": "ط",
    "ﻃ": "ط",
    "ﻄ": "ط",
    "ﻅ": "ظ",
    "ﻆ": "ظ",
    "ﻇ": "ظ",
    "ﻈ": "ظ",
    "ﻉ": "ع",
    "ﻊ": "ع",
    "ﻋ": "ع",
    "ﻌ": "ع",
    "ﻍ": "غ",
    "ﻎ": "غ",
    "ﻏ": "غ",
    "ﻐ": "غ",
    "ﻑ": "ف",
    "ﻒ": "ف",
    "ﻓ": "ف",
    "ﻔ": "ف",
    "ﻕ": "ق",
    "ﻖ": "ق",
    "ﻗ": "ق",
    "ﻘ": "ق",
    "ﻙ": "ک",
    "ﻚ": "ک",
    "ﻛ": "ک",
    "ﻜ": "ک",
    "ﻝ": "ل",
    "ﻞ": "ل",
    "ﻟ": "ل",
    "ﻠ": "ل",
    "ﻡ": "م",
    "ﻢ": "م",
    "ﻣ": "م",
    "ﻤ": "م",
    "ﻥ": "ن",
    "ﻦ": "ن",
    "ﻧ": "ن",
    "ﻨ": "ن",
    "ﻩ": "ه",
    "ﻪ": "ه",
    "ﻫ": "ه",
    "ﻬ": "ه",
    "ﻭ": "و",
    "ﻮ": "و",
    "ﻯ": "ی",
    "ﻰ": "ی",
    "ﻱ": "ی",
    "ﻲ": "ی",
    "ﻳ": "ی",
    "ﻴ": "ی",
    "ﻵ": "لا",
    "ﻶ": "لا",
    "ﻷ": "لا",
    "ﻸ": "لا",
    "ﻹ": "لا",
    "ﻺ": "لا",
    "ﻻ": "لا",
    "ﻼ": "لا",
}

valid_chars = [
    " ",
    #################
    "0",
    "1",
    "2",
    "3",
    "4",
    "5",
    "6",
    "7",
    "8",
    "9",
    "A",
    "B",
    "C",
    "D",
    "E",
    "F",
    "G",
    "H",
    "I",
    "J",
    "K",
    "L",
    "M",
    "N",
    "O",
    "P",
    "Q",
    "R",
    "S",
    "T",
    "U",
    "V",
    "W",
    "X",
    "Y",
    "Z",
    "a",
    "b",
    "c",
    "d",
    "e",
    "f",
    "g",
    "h",
    "i",
    "j",
    "k",
    "l",
    "m",
    "n",
    "o",
    "p",
    "q",
    "r",
    "s",
    "t",
    "u",
    "v",
    "w",
    "x",
    "y",
    "z",
    "آ",
    "ئ",
    "ا",
    "ب",
    "ت",
    "ث",
    "ج",
    "ح",
    "خ",
    "د",
    "ذ",
    "ر",
    "ز",
    "س",
    "ش",
    "ص",
    "ض",
    "ط",
    "ظ",
    "ع",
    "غ",
    "ف",
    "ق",
    "ل",
    "م",
    "ن",
    "ه",
    "و",
    "پ",
    "چ",
    "ژ",
    "ک",
    "گ",
    "ی",
]


def _replace_rep(t):
    "Replace repetitions at the character level: ccc -> c"

    def __replace_rep(m):
        c, cc = m.groups()
        return f"{c}"

    re_rep = re.compile(r"(\S)(\1{2,})")
    return re_rep.sub(__replace_rep, t)


def _replace_wrep(t):
    "Replace word repetitions: word word word -> word"

    def __replace_wrep(m):
        c, cc = m.groups()
        return f"{c}"

    re_wrep = re.compile(r"(\b\w+\W+)(\1{2,})")
    return re_wrep.sub(__replace_wrep, t)


def _normalize_text(x):
    """normalize a sentence"""

    x = str(x)
    x = parsivar_normalizer.normalize(x)  # apply `parsivar` normalizations
    x = re.sub(r"[\u200c\r\n]", " ", x)  # remove half space and new line characters
    x = x.lower()
    x = "".join(
        [char_mappings[xx] if xx in char_mappings else xx for xx in x]
    )  # substitue bad characters with appropriate ones
    x = re.sub(
        r"[^{}]".format("".join(valid_chars)), " ", x
    )  # just keep valid characters and substitue others with space
    x = re.sub(r"[a-z]+", r" \g<0> ", x)  # put space around words and numbers
    x = re.sub(r"[0-9]+", r" \g<0> ", x)  # put space around words and numbers
    x = re.sub(r"\s+", " ", x)  # remove more than one white spaces with space
  #  x = _replace_rep(x) ################################################################################################I change this one
    x = _replace_wrep(x)
    return x.strip()


def normalize_texts(X, use_tqdm=False):
    """normalize list of sentences"""

    if use_tqdm:
        X = [_normalize_text(x) for x in tqdm(X)]
    else:
        X = [_normalize_text(x) for x in X]
    return X

In [ ]:
class JSONListWriter:
    """
    auxilary class to write list of dictionaries into json file.
    each item in one line.
    """

    def __init__(self, file_path):
        self.fd = None
        self.file_path = file_path
        self.delimiter = "\n"

    def open(self):
        self.fd = open(self.file_path, "w")
        self.first_item_written = False
        return self

    def close(self):
        self.fd.close()
        self.fd = None

    def write_item(self, obj):
        if self.first_item_written:
            self.fd.write(self.delimiter)
        self.fd.write(json.dumps(obj))
        self.first_item_written = True

    def __enter__(self):
        return self.open()

    def __exit__(self, type, value, traceback):
        self.close()

In [ ]:
# setting paths for inputs
data_folder = "./data"

products_path = os.path.join(data_folder, "base_products.json")
products_normalized_path = os.path.join(data_folder, "base_products_normalized.json")

search_log_train_path = os.path.join(data_folder, "search_log_train.json")
click_log_train_path = os.path.join(data_folder, "click_log_train.json")

queries_test_offline_path = os.path.join(data_folder, "queries_test_offline.json")
queries_test_offline_normalized_path = os.path.join(
    data_folder, "queries_test_offline_normalized.json"
)

# paths for aggregated data to be maid
search_clicks_file_path = os.path.join(
        data_folder, f"searches_clicks_joined_train.json"
    )

search_click_merged_path = os.path.join(data_folder, f"searches_merged_train.json")

In [ ]:
def make_base_product_names(products_path: str, products_normalized_path: str):
    """
    assign each base product a name.
    it is extracted from sellers of that product.
    """

    with JSONListWriter(products_normalized_path) as file:
        for product in read_json(products_path):
            pr_name = ""
            for seller in product["sellers"]:
                pr_name += " " + seller["name1"] + " " + seller["name2"]
            words = [w.strip() for w in pr_name.split()]
            words = set(
                [w for w in words if w != ""]
            )  # create a set of all words from seller product names
            pr_name = (" ".join(words)).strip()

            if (
                pr_name == ""
            ):  # exclude this product if its name is an empty string (does not have sellers)
                continue

            product["product_name"] = pr_name
            product["product_name_normalized"] = _normalize_text(pr_name)

            file.write_item(product)


def aggregate_clicks(search_path, click_path, tag, valid_base_ids):
    """aggregate clicks on each search record and injects it into the search record"""

    search_clicks_dict = {}
    for i, click_row in enumerate(
        read_json(click_path)
    ):  # aggregate clicks on search_id
        search_id = click_row["search_log_id"]
        base_product_id = click_row["base_product_id"]

        list_of_clicks = search_clicks_dict.get(search_id, [])
        list_of_clicks.append(base_product_id)
        search_clicks_dict[search_id] = list_of_clicks

    invalid_results, invalid_clicks, invalid_searches = 0, 0, 0
    
    with JSONListWriter(
        search_clicks_file_path
    ) as file:  # write the result in a new file
        for i, search_row in enumerate(read_json(search_path)):
            search_id = search_row["_id"]
            search_results = search_row["result"]

            results = [
                r for r in search_results if r in valid_base_ids
            ]  # omit results that are not valid products
            results_set = set(results)

            clicks = search_clicks_dict.get(search_id, [])
            clicks = [
                c for c in clicks if c in results_set
            ]  # omit clicks on invalid products

            invalid_results += len(search_results) - len(results)
            invalid_clicks += len(search_clicks_dict.get(search_id, [])) - len(clicks)

            if len(clicks) == 0:
                invalid_searches += 1
                continue

            search_row["raw_query"] = search_row["raw_query"].strip()
            search_row["raw_query_normalized"] = _normalize_text(
                search_row["raw_query"]
            )  # store the normalized raw_query
            search_row["result"] = results
            search_row["clicks"] = clicks

            file.write_item(search_row)

    print(
        f"invalid searches: {invalid_searches}, "
        + f"invalid results: {invalid_results}, "
        + f"invalid clicks: {invalid_clicks}"
    )


def aggregate_searches(tag):
    "aggregates searches based on raw query."

    search_clicks_path = os.path.join(data_folder, f"searches_clicks_joined_{tag}.json")
    groups = {}
    normalized_query_mapping = {}
    # aggregate searchs on raw_query
    # following counters are creatd for each aggregated search
    # results counter: shows how many times each product is showed to user when the raw_query is searched
    # clicks counter: shows how many times each product is clicked when the raw_query is searched
    # pages counter: shows how many times each page is viewed by user when the raw_query is searched
    for i, search in enumerate(read_json(search_clicks_path)):
        raw_query = search["raw_query"]
        normalized_query_mapping[raw_query] = search["raw_query_normalized"]

        counters = groups.get(raw_query, {})
        groups[raw_query] = counters

        counters.setdefault("results", collections.Counter())
        counters.setdefault("pages", collections.Counter())
        counters.setdefault("clicks", collections.Counter())

        counters["results"].update(search["result"])
        counters["pages"].update([search["page"]])
        counters["clicks"].update(search["clicks"])

    new_df = []
    for raw_query, counters in tqdm(groups.items()):
        results_counter = counters["results"].most_common()  # sort based on views
        pages_counter = counters["pages"].most_common()  # sort based on views
        clicks_counter = counters["clicks"].most_common()  # sort based on clicks

        new_df.append(
            {
                "raw_query": raw_query,
                "raw_query_normalized": normalized_query_mapping[raw_query],
                "results": [k for k, v in results_counter],
                "result_counts": [v for k, v in results_counter],
                "pages": [k for k, v in pages_counter],
                "page_counts": [v for k, v in pages_counter],
                "clicks": [k for k, v in clicks_counter],
                "click_counts": [v for k, v in clicks_counter],
            }
        )
    print("Number of unique queries after merge:", len(new_df))

    pd.DataFrame(new_df).to_json(
        search_click_merged_path,
        orient="records",
        lines=True,
    )


def normalize_test_queries(queries_test_path, queries_test_normalized_path):
    """normalize test queries"""
    with JSONListWriter(queries_test_normalized_path) as file:
        for query in read_json(queries_test_path):
            normalized_query = _normalize_text(query)
            file.write_item(normalized_query)

In [ ]:
make_base_product_names(products_path, products_normalized_path)

print("\nProduct names created and saved in:", products_normalized_path)

1985152it [22:14, 1487.30it/s]


Product names created and saved in: ./data/base_products_normalized.json


In [ ]:
valid_base_ids = set(
    [product["_id"] for product in read_json(products_normalized_path)]
)
print("\nList of valid products created")

1769291it [00:36, 49002.78it/s]



List of valid products created


In [ ]:
normalize_test_queries(queries_test_offline_path, queries_test_offline_normalized_path)
print("Test queries are normalized")

38724it [00:12, 3146.71it/s]

Test queries are normalized


In [ ]:
%reset-f

-----------------------------------------------------------------------

### make new features from pervious datas

In [ ]:
import matplotlib.pyplot as plt
import itertools
from datetime import datetime
import pandas as pd
import numpy as np
import json
import re
import warnings
import gc 
from tqdm import tqdm, trange

In [ ]:
#read data and makeing dataframes
def read_lowmem(path):
  with open(path) as f:
    res = [json.loads(line) for line in tqdm(f)]
    res = pd.DataFrame(res)
  return res 

In [ ]:
 
base_products_normalized = read_lowmem('/content/drive/MyDrive/data_days/base_products_normalized.json')
searches_clicks_joined_train = read_lowmem('/content/drive/MyDrive/data_days/searches_clicks_joined_train.json')
queries_test_offline_normalized = read_lowmem("/content/drive/MyDrive/data_days/queries_test_offline_normalized.json")
queries_test_offline = read_lowmem("/content/drive/MyDrive/data_days/queries_test_offline.json")
#search = read_lowmem('/content/data/search_log_train.json') 


In [ ]:
searches_merged_train =read_lowmem("/content/drive/MyDrive/data_days/searches_merged_train.json")

116621it [00:06, 16938.73it/s]


In [ ]:
queries_test_offline_normalized = read_lowmem("/content/drive/MyDrive/data_days/queries_test_offline_normalized.json")
queries_test_offline = read_lowmem("/content/drive/MyDrive/data_days/queries_test_offline.json")
base_products_normalized = read_lowmem('/content/drive/MyDrive/data_days/base_products_normalized.json')



38724it [00:00, 265221.35it/s]
38724it [00:00, 252077.33it/s]
1769291it [00:51, 34106.35it/s]


In [ ]:
click =read_lowmem("/content/drive/MyDrive/data_days/click_log_train.json")

In [ ]:
#read data and makeing dataframes
def read_lowmem(path):
  with open(path) as f:
    res = [json.loads(line) for line in tqdm(f)]
    res = pd.DataFrame(res)
  return res  
base_products_normalized = read_lowmem('/content/data/base_products_normalized.json')
click = read_lowmem('/content/data/click_log_train.json') 
queries_test_offline_normalized = read_lowmem("/content/data/queries_test_offline_normalized.json")
queries_test_offline = read_lowmem("/content/data/queries_test_offline.json")
#search = read_lowmem('/content/data/search_log_train.json') 


1769291it [00:46, 37848.60it/s]
6317934it [00:29, 211050.06it/s]
38724it [00:00, 250448.68it/s]
38724it [00:00, 244561.63it/s]


In [ ]:
search_log_train= read_lowmem('/content/drive/MyDrive/data_days/search_log_train.json')

3694579it [00:48, 76408.68it/s] 


In [ ]:
click= read_lowmem('/content/drive/MyDrive/data_days/click_log_train.json')

6317934it [00:35, 177211.45it/s]


In [ ]:
#extraction of number of clicks
#click.drop_duplicates(subset=['base_product_id' , 'search_log_id'] ,keep='last' , inplace=True) #Eliminate extra rows
df_nclick = pd.DataFrame(click['base_product_id'].value_counts()) 
del click
gc.collect()
df_nclick .head()

In [ ]:
df_nclick .head()

base_product_id
mmmzj            25125
mmtqd            21470
mmmbo            20736
mmmbi            20017
mmmbw            19833

In [ ]:
base_products_normalized.head()

_id  ...                            product_name_normalized
0  yxwrs  ...  رزولوشن hd 142 x دیتا hd video 1920 x 1080 3 d...
1  mbeby  ...  گرم ژل lash essence and essence لیفت اصلی ژل m...
2  yovgc  ...  40 رکسونا rexona استیک گرم دیودورانت وی مدل مر...
3  yokff  ...  algodon استیک 40 dry استیک الگودون rexona rexo...
4  uduyq  ...  y 550 گوشی مدل اسند موبایل ascend y 550 huawei...

[5 rows x 5 columns]

###delete extera words
delete extera words in each product name nomalized

In [ ]:
def eli_dup(string):
  s = ' '
  my_list = string.split()
  my_final_list = set(my_list)
  lst = list(my_final_list)
  return  s.join(lst)

In [ ]:
base_products_normalized['product_name_normalized'] = base_products_normalized['product_name_normalized'].apply(eli_dup)
base_products_normalized['product_name'] = base_products_normalized['product_name'].apply(eli_dup)



```
# This is formatted as code
```

### sort by number of click and category name
sort base_products_normalized by number of clicks and category name

In [ ]:
###########################################################################################

In [ ]:
base_products_normalized['click_number'] = base_products_normalized['_id'].apply(lambda x: df_nclick['base_product_id'].loc[x] if x in df_nclick.index else 0)
base_products_normalized.sort_values(by=["category_name","click_number" ] ,ascending=False, inplace=True)
base_products_normalized.reset_index(inplace = True)

del df_nclick
gc.collect()

--------------------------------------------------------------------

### define necessery functions


In [ ]:
# correction function used for correct bad query serches
#ab c   d --> ab c d
#si9 تن9 --> si 9 9 تن
#and delete Effectless words in invalid words
invalid_words = ["خرید", "دانلود",' ' ,"برای","/" , "\\" , "ا","ض","ص","ث","ق","ف","غ","ع","ه","خ","ح","ج","چ","پ","ش","س","ی","ب","ل","ت","ن","م","ک","گ",";","'" , "ظ","ط","ز","ر","ذ","د","ئ","و","."]
invalid_words = set(invalid_words)
invalid_words = list(invalid_words)

def split(word):
    return [char for char in word]


def correction (text):
  text = text.split(" ")
  invalid_words_lenght = len(invalid_words)
  c_text = []
  k = 0
  for j in text :
    k = 0
    for i in range(invalid_words_lenght) :
      if invalid_words[i] == j or j== '' :
        k=1
        pass
        
      elif i == invalid_words_lenght-1 and k==0:
        
        c_text.append(j)
        
  text = " ".join(c_text)
 
  
  text = split(text) 
  lenght_text = len(text)
  for i in range(lenght_text):
    if i == lenght_text-1 :
      break
    if text[i] in "aqzwsxedcrfvtgbyhnujmikolp1234567890" and text[i+1] in "ضشظصسطثیزقبرفلذغادعتئهنخمحکجچپگکو" :
      text.insert( i+1 , " ")
    if text[i] in "ضشظصسطثیزقبرفلذغادعتئهنخمحکجچپگکو1234567890" and text[i+1] in "aqzwsxedcrfvtgbyhnujmikolp" :
      text.insert( i+1 , " ")
  text ="".join(text)


  return text

---------------------------------------------

##apply correction function to query serach normalized

In [ ]:
#      tedad bishtar ghalat emlayii 

In [ ]:
queries_test_offline.head(10)

0
0         تلویزیون 40 ایتچ
1          قهوه سازDelongi
2       بند فلزی mi band 5
3            قالی زمردمشهد
4               پوکوx3 pro
5     Xiaomi redmi note 9s
6                    4000d
7                 لباس آنا
8              سنگ چشم ببر
9  گلگیر جلو پژو ۴۰۵ شرکتی

In [ ]:
base_products_normalized.head(3)

_id  ...                            product_name_normalized
0  yxwrs  ...  1920 x 1080 hd مدل سینمای ویدیو dlp اصلی video...
1  mbeby  ...  حجم کننده essence mascara ژل essence and masca...
2  yovgc  ...  رکسونا دیودرانت men deodorant دیودورانت مدل گر...

[3 rows x 5 columns]

In [ ]:
base_products_normalized.head()

_id  ...                            product_name_normalized
0  yxwrs  ...  1920 x 1080 hd مدل سینمای ویدیو dlp اصلی video...
1  mbeby  ...  حجم کننده essence mascara ژل essence and masca...
2  yovgc  ...  رکسونا دیودرانت men deodorant دیودورانت مدل گر...
3  yokff  ...  حجم رکسونا دیودرانت 40 ml deodorant رول dry مد...
4  uduyq  ...  موبایل ascend huawei گوشی اسند huawei ascend م...

[5 rows x 5 columns]

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer

In [ ]:
searches_clicks_joined_train.head(2)

_id  ...                 clicks
0  609d7e3a6c2e88f6b241b089  ...  [mmmmb, mmmmb, mmmmb]
1  609d7e4802589dff17211ce4  ...                [mmmmw]

[2 rows x 7 columns]

In [ ]:
searches_merged_train.head(2)

raw_query  ...                                       click_counts
0  گوشی موبایل  ...  [441, 369, 314, 286, 272, 245, 243, 229, 185, ...
1         گوشی  ...  [3184, 2749, 1819, 1727, 1709, 1485, 1336, 128...

[2 rows x 8 columns]

In [ ]:
base_products_normalized.head()

_id  ...                            product_name_normalized
0  yxwrs  ...  1920 x 1080 hd مدل سینمای ویدیو dlp اصلی video...
1  mbeby  ...  حجم کننده essence mascara ژل essence and masca...
2  yovgc  ...  رکسونا دیودرانت men deodorant دیودورانت مدل گر...
3  yokff  ...  حجم رکسونا دیودرانت 40 ml deodorant رول dry مد...
4  uduyq  ...  موبایل ascend huawei گوشی اسند huawei ascend م...

[5 rows x 5 columns]

In [ ]:
base_products_normalized.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1769291 entries, 0 to 1769290
Data columns (total 5 columns):
 #   Column                   Dtype 
---  ------                   ----- 
 0   _id                      object
 1   category_name            object
 2   sellers                  object
 3   product_name             object
 4   product_name_normalized  object
dtypes: object(5)
memory usage: 67.5+ MB


In [ ]:
base_products_normalized['category_name'].value_counts()

کتاب و مجلات                               73853
کیف و کاور گوشی و تبلت                     53176
ساعت مچی عقربه‌ ای و دیجیتالی              39647
سایر لوازم یدکی خودرو                      34473
سایر ابزار دستی و تجهیزات کارگاهی          32575
                                           ...  
پرینتر پاناسونیک                               1
کامپیوتر دسکتاپ تارکس                          1
سیستم‌های نظارتی و امنیتی و لوازم جانبی        1
دکوراسیون منزل                                 1
مسیریاب خودرو                                  1
Name: category_name, Length: 1554, dtype: int64

In [ ]:
Category = pd.DataFrame(base_products_normalized['category_name'].value_counts() )

In [ ]:
Category.reset_index(inplace=True)

In [ ]:
base_products_normalized.head()

_id  ...                            product_name_normalized
0  yxwrs  ...  1920 x 1080 hd مدل سینمای ویدیو dlp اصلی video...
1  mbeby  ...  حجم کننده essence mascara ژل essence and masca...
2  yovgc  ...  رکسونا دیودرانت men deodorant دیودورانت مدل گر...
3  yokff  ...  حجم رکسونا دیودرانت 40 ml deodorant رول dry مد...
4  uduyq  ...  موبایل ascend huawei گوشی اسند huawei ascend م...

[5 rows x 5 columns]

###method 1

In [ ]:
dontknow =  []
for i in tqdm(Category['index'])  :
  df  = base_products_normalized[base_products_normalized['category_name'] == i]
  c = ""

  for j in df['product_name_normalized']:
    c+= j
  dontknow.append(c)




100%|██████████| 1554/1554 [04:04<00:00,  6.35it/s]


In [ ]:
dontknow[0]

'باستان کتاب دانستنی از هایی ایرانپژوهشی و کتاب منظ د ازا سنت باغ سازی در پاریقل کتاب کدو زن قلیختم کتاب الجنان سوره ان منتخب با همراه مفاتیحکتاب بی از های جونز قلنبه جونی مهمانی مجموعه بالشهای کتاب سفری اسمان کامل بر کن نیایش مجموعهتعقیب گریز و کتاب از مدرسه جاسوسی جنوب در مجموعهو کتاب نوجوان تربیت بهترین برای از تغذیه کودک کودکان کلیدهای مجموعه نوجوانانکتاب ها اربابنقاب کتاب از نقره ای مجیستریوم مجموعهصلاح جات کتاب امنه اهایکتاب سنگین استقلال جنگ چچن بهایمخملک جنازه اشپزشعبده باز فیل اقایاسلام ایینهاین دوچرخه جنون داردمادرید کتاب ریال راهکریم کتاب قرانو کتاب حلزون از سوفی مجموعهکتاب چه سوی شمایل گوارا انکتاب دریایی مصور دزدان دانشنامهکتاب قلعه حیواناتترسناک کتاب واقعیت کسی دارن را از تر چه شانی کتاب جن از قورباغه ربایی زده ارمنته مجموعهدارویی راهنمای کتاب پزشکی راهنمای خا خانوادهکتاب روایتی کیمیا دختر سرگذشت بر دوست خواندهکتاب جادو کوهدایره کتاب ارتباط نخستین بدن انسان المعارف بدایره کتاب با ارتباط جانوران نخستین المعارفکتاب اهن قراضه نان مجموعه خشک دمپایی کهنهکتاب 3 های کاردستی اوری

In [ ]:
len(dontknow)

1554

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer


In [ ]:
invalid_words = ["خرید", "دانلود",' ' ,"برای","/" , "\\" , "ا","ض","ص","ث","ق","ف","غ","ع","ه","خ","ح","ج","چ","پ","ش","س","ی","ب","ل","ت","ن","م","ک","گ",";","'" , "ظ","ط","ز","ر","ذ","د","ئ","و","."]


In [ ]:
vectorizer = TfidfVectorizer(lowercase=True, use_idf=True ,stop_words= invalid_words )

In [ ]:
vectorizer.fit(dontknow)

In [ ]:
queries_test_offline_normalized.head()

0
0    تلویزیون 40 ایتچ
1    قهوه ساز delongi
2  بند فلزی mi band 5
3       قالی زمردمشهد
4        پوکو x 3 pro

In [ ]:
responce = vectorizer.transform(['پوکو x 3 pro' ] )
for col in responce.nonzero()[1]:
    print (feature_names[col], ' - ', responce[0, col])

پوکو  -  0.9460017872024833
pro  -  0.32416140826709655


In [ ]:
responce = vectorizer.transform(['بند فلزی mi band 5'] )
for col in responce.nonzero()[1]:
    print (feature_names[col], ' - ', responce[0, col])

فلزی  -  0.3711638743627793
بند  -  0.4525721914225984
mi  -  0.48579221642179754
band  -  0.6491700180869071


In [ ]:
responce = vectorizer.transform(['قهوه ساز delongi' ] )
for col in responce.nonzero()[1]:
    print (feature_names[col], ' - ', responce[0, col])

قهوه  -  0.27923514063934785
ساز  -  0.3104619548700001
delongi  -  0.9086479575778629


In [ ]:
search_click_merge_2.iloc[247:249]

raw_query_normalized  ... tf-idf_priority
247                  5 3  ...           [100]
248                  5 g  ...              []

[2 rows x 4 columns]

In [ ]:
responce = vectorizer2.transform(['lug piop']  , )
for col in responce.nonzero()[1]:
    print (feature_names[col], ' - ', responce[0, col])

lug  -  1.0


###method 2

In [ ]:
dontknow2 =  []
for i in tqdm(base_products_normalized['product_name_normalized'])  :
  dontknow2.append(i)




100%|██████████| 1769291/1769291 [00:03<00:00, 544854.57it/s] 


In [ ]:
vectorizer2 = TfidfVectorizer(lowercase=True, use_idf=True ,stop_words= invalid_words )
vectorizer2.fit(dontknow2)
feature_names = vectorizer2.get_feature_names()


In [ ]:
responce = vectorizer2.transform(['پوکو x 3 pro' ] )
for col in responce.nonzero()[1]:
    print (feature_names[col], ' - ', responce[0, col])

پوکو  -  0.8899441920423984
pro  -  0.45606944103941327


In [ ]:
responce = vectorizer2.transform(['بند فلزی mi band 5'] )
for col in responce.nonzero()[1]:
    print (feature_names[col], ' - ', responce[0, col])

فلزی  -  0.459435878265007
بند  -  0.4592482489749901
mi  -  0.5012877094937298
band  -  0.5715945695042921


In [ ]:
responce = vectorizer2.transform(['قهوه ساز delongi' ] )
for col in responce.nonzero()[1]:
    print (feature_names[col], ' - ', responce[0, col])

قهوه  -  0.37157890150997963
ساز  -  0.3882606417335175
delongi  -  0.8433165443849148


###save datas in workspace to free memory


In [ ]:
base_products_normalized.to_csv("base_products_normalized.csv")
queries_test_offline_normalized.to_csv("queries_test_offline_normalized.csv")


In [ ]:
#from google.colab import drive
#drive.mount('/content/drive')

In [ ]:
!cp queries_test_offline_normalized.csv /content/drive/MyDrive
!cp base_products_normalized.csv /content/drive/MyDrive

cp: cannot create regular file '/content/drive/MyDrive': No such file or directory
cp: cannot create regular file '/content/drive/MyDrive': No such file or directory


In [ ]:
%reset -f # reset notebook due to memory limitations


Don't know how to reset  #, please run `%reset?` for details
Don't know how to reset  reset, please run `%reset?` for details
Don't know how to reset  notebook, please run `%reset?` for details
Don't know how to reset  due, please run `%reset?` for details
Don't know how to reset  to, please run `%reset?` for details
Don't know how to reset  memory, please run `%reset?` for details
Don't know how to reset  limitations, please run `%reset?` for details


In [ ]:
%reset

Once deleted, variables cannot be recovered. Proceed (y/[n])? y


In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from tqdm import tqdm, trange
import json

In [ ]:
base_products_normalized = pd.read_csv("/content/base_products_normalized.csv" )
base_products_normalized.drop(["index" ,"Unnamed: 0" ] , axis=1 ,inplace=True)
base_products_normalized.head(2)

_id  ... click_number
0  mguae  ...           68
1  mujip  ...           58

[2 rows x 6 columns]

###Dictionry
make a dictionry by using words in product_name_normalized

In [ ]:
base_products_normalized.head()

_id           category_name  ...     price    date_added
0  yxwrs    ویدیو پروژکتور اپتما  ...  31852600  1.528652e+09
1  mbeby  تقویت کننده مژه و ابرو  ...     60000  1.593461e+09
2  yovgc             مام و اسپری  ...         0  1.588267e+09
3  yokff             مام و اسپری  ...     49000  1.586876e+09
4  uduyq              گوشی هوآوی  ...         0  1.493062e+09

[5 rows x 7 columns]

In [ ]:
df = base_products_normalized.copy()

In [ ]:
df['list'] = df['product_name_normalized'].apply(lambda x:x.split(" "))
df.head()

_id  ...                                               list
0  yxwrs  ...  [پروژکتور, دیتا, video, 3000, 3, dlp, optoma, ...
1  mbeby  ...  [brow, مژه, گرم, و, اورجینال, mascara, کننده, ...
2  yovgc  ...  [وی, deodorant, گرم, تعریق, ایت, men, دیودرانت...
3  yokff  ...  [میلی, deodorant, کاتن, کاتون, لیتر, گرم, تعری...
4  uduyq  ...  [اسند, y, موبایل, ascend, گوشی, مدل, huawei, g...

[5 rows x 8 columns]

In [ ]:
df.iloc[4 , 4]

'اسند y موبایل ascend گوشی مدل huawei g وای هواوی 4 550'

In [ ]:
df1 = df[['category_name', 'list']].copy()


In [ ]:
df1.iloc[4 , 1]

['اسند',
 'y',
 'موبایل',
 'ascend',
 'گوشی',
 'مدل',
 'huawei',
 'g',
 'وای',
 'هواوی',
 '4',
 '550']

In [ ]:
df1.head()

category_name                                               list
0    ویدیو پروژکتور اپتما  [پروژکتور, دیتا, video, 3000, 3, dlp, optoma, ...
1  تقویت کننده مژه و ابرو  [brow, مژه, گرم, و, اورجینال, mascara, کننده, ...
2             مام و اسپری  [وی, deodorant, گرم, تعریق, ایت, men, دیودرانت...
3             مام و اسپری  [میلی, deodorant, کاتن, کاتون, لیتر, گرم, تعری...
4              گوشی هوآوی  [اسند, y, موبایل, ascend, گوشی, مدل, huawei, g...

In [ ]:
#Extention of search to make faster process
from itertools import chain
df_extended = pd.DataFrame({
    'category_name':df1['category_name'].values.repeat(df1['list'].str.len()),
    'list':list(chain.from_iterable(df1['list'].tolist()))
})

In [ ]:
df_extended[df_extended['list'] == 'اینچ']

category_name  list
765                    سایر ماشین‌های اداری  اینچ
1784                       تلویزیون سامسونگ  اینچ
1953                       تلویزیون جی پلاس  اینچ
2725            سایر تلویزیون و لوازم جانبی  اینچ
6894                       تلویزیون جی پلاس  اینچ
...                                     ...   ...
15286538                   تلویزیون جی پلاس  اینچ
15286755                    نمایشگر سامسونگ  اینچ
15286800                    نمایشگر سامسونگ  اینچ
15287149  سایر ابزار دستی و تجهیزات کارگاهی  اینچ
15290280                 ساب و بلندگو خودرو  اینچ

[16130 rows x 2 columns]

In [ ]:
lst  = list(df_extended["list"])
lst.sort()
lst = list(set(lst))
lst.sort()

In [ ]:
lst[0:5]

['0', '00', '000', '0000', '00000']

In [ ]:
dic = {'ا': [],
       'ب': [],
       'پ': [],
       'ت': [],
       'ث': [],
       'ج': [],
       'چ': [],
       'ح': [],
       'خ': [],
       'د': [],
       'ذ': [],
       'ر': [],
       'ز': [],
       'ژ': [],
       'س': [],
       'ش': [],
       'ص': [],
       'ض': [],
       'ط': [],
       'ظ': [],
       'ع': [], 
       'غ': [],
       'ف': [],
       'ق': [],
       'ک': [],
       'گ': [],
       'ل': [],
       'م': [],
       'ن': [],
       'و': [],
       'ه': [],
       'ی': [],
       'آ' : [],
       'a': [],
       'b' :[] ,
       'c': [],
       'd': [],
       'e': [],
       'f': [],
       'g': [],
       'h': [],
       'i': [],
       'j': [],
       'k': [],
       'l': [],
       'm': [],
       'n': [],
       'o': [],
       'p': [],
       'q': [],
       'r': [],
       's': [],
       't': [],
       'u': [],
       'v': [],
       'w': [], 
       'x': [],
       'y': [],
       'z': [],
       '1': [],
       '2': [],
       '3': [],
       '4': [],
       '5': [],
       '6': [],
       '7': [],
       '8': [],
       '9': [],
       '0':[],
       '.':[],
       'else':[]}

In [ ]:
df_lst = pd.DataFrame({'product' : lst})
df_lst.head()

product
0       0
1      00
2     000
3    0000
4   00000

In [ ]:
for i in (df_lst['product']):
  for j in list(dic.keys()):
    if (i[0] == j):
      dic[j].append(i)
      break
    if j == 'else':
      dic['else'].append(i)

In [ ]:
sum = 0
for i in dic.keys():
  sum = sum + len(dic[i])
sum   # it must be 278902         

282233

In [ ]:
del sum , df  , df1 , df_lst
gc.collect()

325

####matching
this function used for find proper words that is most similar to query search

###algorithm
in this sectoin we made our algorithm

frist of all we made a dataframe 
dataframe contain category_name 
and all of words that exist in category

In [ ]:
df_listed_name = pd.DataFrame(df_extended.groupby('category_name')['list'].apply(list))

In [ ]:
df_listed_name.head(3)

list
category_name                                                                       
آب انارگیری                        [negin, دستی, اب, انار, گیری, مدل, نگین, گیر, ...
آب سردکن و تصفیه آب و لوازم جانبی  [تصفیه, فیلتر, اب, سطلی, سوبو, a, کوچک, 928, ت...
آب مرکبات‌گیری                     [tefal, press, مرکبات, اب, پرتقال, zp, citrus,...

In [ ]:
del df_extended
gc.collect()

208

now we count how much each word repeat in df_listed_name

In [ ]:
from collections import Counter
def con (x):
  x = Counter(x)
  x = dict(x)
  return x


In [ ]:
df_listed_name['dic'] =  df_listed_name['list'].apply(con)


In [ ]:
df_listed_name.reset_index(inplace=True)

In [ ]:
df_listed_name.head()

category_name  ...                                                dic
0                        آب انارگیری  ...  {'negin': 1, 'دستی': 8, 'اب': 10, 'انار': 9, '...
1  آب سردکن و تصفیه آب و لوازم جانبی  ...  {'تصفیه': 791, 'فیلتر': 478, 'اب': 805, 'سطلی'...
2                     آب مرکبات‌گیری  ...  {'tefal': 1, 'press': 62, 'مرکبات': 269, 'اب':...
3                           آب معدنی  ...  {'اب': 70, '6': 17, 'لیتری': 35, 'معدنی': 66, ...
4                 آباژور و چراغ خواب  ...  {'چراغ': 792, 'خواب': 760, 'نگهبان': 3, 'سگ': ...

[5 rows x 3 columns]

In [ ]:
!pip install parsivar
!wget https://www.dropbox.com/s/tlyvnzv1ha9y1kl/spell.zip
!pip install pyspellchecker
!mkdir /usr/local/lib/python3.7/dist-packages/parsivar/resource/spell 
!unzip spell.zip -d /usr/local/lib/python3.7/dist-packages/parsivar/resource/spell

     |████████████████████████████████| 36.2 MB 56 kB/s 
     |████████████████████████████████| 1.5 MB 37.8 MB/s 
  Created wheel for parsivar: filename=parsivar-0.2.3-py3-none-any.whl size=36492971 sha256=621230b05814f54b04c70bbc935eb53782839e48961f4db0783ff1cc15c41aff
  Stored in directory: /root/.cache/pip/wheels/ae/67/7a/49cbf08f64d3f76a26eceaf0e481a40e233f05d4356875cbed
  Created wheel for nltk: filename=nltk-3.4.5-py3-none-any.whl size=1449922 sha256=d28eab5c73b5ff78c5674fbcf6f8a528e0de4f233a1e577c7a569c7aba8b84f2
  Stored in directory: /root/.cache/pip/wheels/48/8b/7f/473521e0c731c6566d631b281f323842bbda9bd819eb9a3ead
Successfully built parsivar nltk
  Attempting uninstall: nltk
    Found existing installation: nltk 3.2.5
    Uninstalling nltk-3.2.5:
      Successfully uninstalled nltk-3.2.5
--2021-09-02 16:58:33--  https://www.dropbox.com/s/tlyvnzv1ha9y1kl/spell.zip
Resolving www.dropbox.com (www.dropbox.com)... 162.125.81.18, 2620:100:6035:18::a27d:5512
Connecting to www.drop

In [ ]:
from parsivar import SpellCheck
myspell_checker = SpellCheck()
spell_checker = myspell_checker.spell_corrector("کیبرد")      #good enough
spell_checker

'کی برد'

####matching
this function used for find proper words that is most similar to query search

In [ ]:
  #splell cheker add konam va be matchin ezaf konam     test konam کیبردبلوتوثی dar spell chi mishe

In [ ]:
def split(word ):
    return [char for char in word]
def matching3 (tex ):
  texted = tex.split(" ")
  len_tex = len(texted)
  c_text = []
  extera = ''
  extera_2 = ''
  m=0
  for text in texted:
    text_r = text
    text = split(text)
    l = len(text)
    q=0
    p = 100 / l
    com_f = 0
    ten =0
    search = dic[text[0]]
    #print(search)
    correct_text = ""
    for s in search:
      com = 0 
      te = 0
     
      
      l_s = len(s)
      i = -1
      for j in range(l_s):
         i+=1
         if i >= l :
           break
         if text[j] == s[j] :
           com+=p
           te +=1
         else:
           te-=1
      if l == l_s  and com>= (l-1)*p-5 :
        #print(l,'--',l_s ,'--',com)
        com+=3
      if l_s > l :
        com = com - (l_s-l)*p
      if com >= 99 :
        correct_text=s
        break
      try:
          if l_s == te and te>ten and te>=3   :       #te>4   beacuse of bad dictionry
              ten = te
              text_r_ = split(text_r)
              text_r_.insert(l_s , " ")
              extera = "".join(text_r_)
              
              extera = matching2(extera)
      except:
        pass     
     
      if com > com_f and com >=70:               # 50 or 45 its diffrent answers
       com_f = com
       correct_text = s
       #print(l_s,s)
       
      if s == search[-1] and extera!='' and com_f<70:
        correct_text = extera.split(' ')
        c_text.append(correct_text[0])
        correct_text = correct_text[1]
      if com> com_f:
        com_f = com
        extera_2 = s
       
    if correct_text == '':
        correct_text = extera_2
    c_text.append(correct_text)   
      
  c_text = " ".join(c_text) 

  return c_text

  

In [ ]:
def split(word):
    return [char for char in word]
def matching (tex):
  texted = tex.split(" ")
  c_text = []
  
  for text in texted:
    
    text = split(text)
    l = len(text)
    p = 100 / l
    com_f = 0
    
    search = dic[text[0]]
    correct_text = ""
    for s in search:
      com = 0 
      i = -1
      for j in range(len(s)):
       i += 1
       if i == l :
          break
       if text[i] == s[j] :
         com+=p
      # if l == len(s):
      #   com+=5
      if com >= 99 :
        correct_text=s
        
        break
      if com > com_f and com >=45 :               # 50 or 45 its diffrent answers
       com_f = com
       correct_text = s
       
    c_text.append(correct_text)   
      
  c_text = " ".join(c_text) 
  return c_text

In [ ]:
def matching2 (tex ):
  texted = tex.split(" ")
  len_tex = len(texted)
  c_text = []
  extera = ''
  for text in texted:
    text_r = text
    text = split(text)
    l = len(text)
    
    p = 100 / l
    com_f = 0
    
    search = dic[text[0]]
    correct_text = ""
    for s in search:
      com = 0 
      te = 0
      i = -1
      l_s = len(s)
      for j in range(l_s):
         i += 1
         if i == l :
           break
         if text[i] == s[j] :
           com+=p
           te +=1
      if com == 100 :
        correct_text=s
        break

      if com > com_f and com >=99 :               # 50 or 45 its diffrent answers
       com_f = com
       correct_text = s
       
           
       
    c_text.append(correct_text)   
      
  c_text = " ".join(c_text) 

  return c_text

in this block we apply matging and parsivar to correct words
we use this structure

if matchin i != i
  
  d = myspell_checker.spell_corrector(i)       
 
  d = matching(d)            

In [ ]:
queries_test_offline_normalized = read_lowmem("/content/drive/MyDrive/data_days/queries_test_offline_normalized.json" )
#queries_test_offline_normalized.drop(['Unnamed: 0'] , inplace=True , axis=1)
queries_test_offline_normalized.head(2)

38724it [00:00, 235814.05it/s]


0
0  تلویزیون 40 ایتچ
1  قهوه ساز delongi

In [ ]:
def sent (text):
  j=0
  text = str(text)
  text = text.split(" ")
  text2 = []
  
  for i in text:
    #d = myspell_checker.spell_corrector(i)
    #if i!= d :
    d = matching(i )  
    if d!=i :
      d = myspell_checker.spell_corrector(i)
      d = matching(d )
      text2.append(d)  
    else:
      text2.append(d)
  text2 = " ".join(text2)

  return text2

In [ ]:
#this block used to  obtain time of process 
#so all of the query search take 9 minute to finish
ss = queries_test_offline_normalized[0:100].copy()

In [ ]:
ss.columns = ['0']

In [ ]:
ss

0
0      تلویزیون 40 ایتچ
1      قهوه ساز delongi
2    بند فلزی mi band 5
3         قالی زمردمشهد
4          پوکو x 3 pro
..                  ...
95      ماژول پاور بانک
96         مورم ایرانسل
97           nokia 5310
98       اداپتور 12 ولت
99  لوازم اسپرت پژو 405

[100 rows x 1 columns]

In [ ]:
ss['1'] = ss['0'].apply(lambda x:sent(x))

In [ ]:
ss[ss['0']!=ss['1']]

0                            1
0             تلویزیون 40 ایتچ             تلویزیون 40 اینچ
3                قالی زمردمشهد               قالی زمرد مشهد
10                   فیس برواش                   فیس بر واش
35                  اسباب بازز                   اسباب با ز
37               شیاعومی نوت 8            شیا عامیانه نوت 8
45                    مونوپولب                     مونوپولی
51                   چراغ پارش                    چراغ پارس
70           دسته پابجی موبایا            دسته پابجی موبایل
71              جامایع ظرقشویی               جامایع ظرفشویی
74  صندل ودمپایی دخترانه زنانه  صندل و دمپایی دخترانه زنانه
82                    جاردبرقی                     جاروبرقی
85                      طمعدان                      طمع دان
87        شیامی ردنی نوت 8 پرو         شیامی مدنی نوت 8 پرو
91                کمپروسر کولر                کمپر وسر کولر
96                مورم ایرانسل                 مورد ایرانسل

In [ ]:
del ss
gc.collect()

563

In [ ]:
queries_test_offline_normalized.columns = ['0']

In [ ]:
queries_test_offline_normalized['2'] = queries_test_offline_normalized['0'].apply(lambda x:sent(x))

In [ ]:
queries_test_offline_normalized.head()

0                   2
0    تلویزیون 40 ایتچ    تلویزیون 40 اینچ
1    قهوه ساز delongi    قهوه ساز delongi
2  بند فلزی mi band 5  بند فلزی mi band 5
3       قالی زمردمشهد      قالی زمرد مشهد
4        پوکو x 3 pro        پوکو x 3 pro

now we made all of priority base on each query

In [ ]:
# this function obtain a list
# this list used for obtain priority of words in search query
def priority (search):
  search = search.split(' ')
  Length = len(search)
  a = 1.3
  s = 0 
 
  for i in range(Length):
    s = s + pow(a,i)
    if i == Length:
      break 
  j = [100/s]
  for i in range(1, Length):
    j.append(j[i-1]*a)
  j  = Reverse (j)
  return j

def Reverse(lst):
    return [ele for ele in reversed(lst)]

make priority of each query so we our algorithm doesn't need to 
process it each  time

In [ ]:
#            queries_test_offline_normalized['3'] = queries_test_offline_normalized['2'].apply(priority)

In [ ]:
queries_test_offline_normalized.head(3)

0                   2
0    تلویزیون 40 ایتچ    تلویزیون 40 اینچ
1    قهوه ساز delongi    قهوه ساز delongi
2  بند فلزی mi band 5  بند فلزی mi band 5

###use tfidf for priority

In [ ]:
feature_names = vectorizer2.get_feature_names()
def tfidf_priority (text) :
  
  responce = vectorizer2.transform([text])
  responce_ = text.split(' ')
  P = []
  N = []
  
  for col in responce.nonzero()[1]:
    P.append(responce[0, col])
    N.append(feature_names[col])
    
  if P == [] or N == []:
    return priority(text)
  
  pri  = []
  
  q = -1 
  for j in responce_:
    q = -1 
    for k in N:
      q+=1
      if k==j :
         pri.append(P[q])
         break
      elif q == len(N)-1 :
        pri.append(0)
  return pri

In [ ]:
responce = vectorizer2.transform(['پوکو x 3 pro' ] )
for col in responce.nonzero()[1]:
    print (feature_names[col], ' - ', responce[0, col] , col)

پوکو  -  0.8899441920423984 269772
pro  -  0.45606944103941327 164616


In [ ]:
tfidf_priority('قالی زمرد مشهد')

[0.6216100066688267, 0.5564919890738858, 0.5512872805586678]

In [ ]:
queries_test_offline_normalized['3'] = queries_test_offline_normalized['2'].apply(tfidf_priority)

In [ ]:
queries_test_offline_normalized.head()

0  ...                                                  3
0    تلویزیون 40 ایتچ  ...  [0.6445719650479241, 0.5490981558649192, 0.531...
1    قهوه ساز delongi  ...  [0.37157890150997963, 0.3882606417335175, 0.84...
2  بند فلزی mi band 5  ...  [0.4592482489749901, 0.459435878265007, 0.5012...
3       قالی زمردمشهد  ...  [0.6216100066688267, 0.5564919890738858, 0.551...
4        پوکو x 3 pro  ...    [0.8899441920423984, 0, 0, 0.45606944103941327]

[5 rows x 3 columns]

In [ ]:
queries_test_offline_normalized.to_csv('queries_tfidf1.csv')

In [ ]:
!cp queries_tfidf1.csv /content/drive/MyDrive/data_days

In [ ]:
queries_test_offline_normalized.head(10)

0  ...                                                  3
0         تلویزیون 40 ایتچ  ...  [0.6445719650479241, 0.5490981558649192, 0.531...
1         قهوه ساز delongi  ...  [0.37157890150997963, 0.3882606417335175, 0.84...
2       بند فلزی mi band 5  ...  [0.4592482489749901, 0.459435878265007, 0.5012...
3            قالی زمردمشهد  ...  [0.6216100066688267, 0.5564919890738858, 0.551...
4             پوکو x 3 pro  ...    [0.8899441920423984, 0, 0, 0.45606944103941327]
5    xiaomi redmi note 9 s  ...  [0.5709551046579694, 0.5892773172308707, 0.571...
6                   4000 d  ...                                           [1.0, 0]
7                 لباس انا  ...           [0.5710109318623898, 0.8209424557748523]
8              سنگ چشم ببر  ...  [0.5088307384548557, 0.4944385358457975, 0.704...
9  گلگیر جلو پژو 405 شرکتی  ...  [0.5538573951207876, 0.3678219081081493, 0.381...

[10 rows x 3 columns]

In [ ]:
a = [2,3,4]
a = [element * 2 for element in a]
max(a)

8

In [ ]:
def x100 (L):
  sum = 0 
  for i in L:
    sum+=i
  
  a = [element *100/sum for element in L]
  return a

In [ ]:
queries_test_offline_normalized['3'] = queries_test_offline_normalized['3'].apply(x100)

In [ ]:
queries_test_offline_normalized[30:40]

0  ...                                                  3
30                   لیدوکایین  ...                                            [100.0]
31              چسب ترمیم شیشه  ...  [31.66854253864878, 39.81686379526179, 28.5145...
32                جارو برقی lg  ...  [37.26937893010778, 28.25724047418974, 34.4733...
33               گوشی a 52 5 g  ...  [35.865937549859446, 0.0, 64.13406245014056, 0...
34             هندزفری سیم دار  ...  [40.53479207916956, 32.10032500612229, 27.3648...
35                  اسباب بازز  ...         [59.1413623833811, 40.85863761661891, 0.0]
36               بازی پی اس فر  ...  [20.737757795524587, 24.054700460799495, 23.99...
37               شیاعومی نوت 8  ...  [37.39718954819271, 40.49986066924627, 22.1029...
38  کاور نوکیا سامسونگ b 310 e  ...  [21.59619568769221, 27.994933072078307, 18.339...
39                 شیایومی x 3  ...                                  [100.0, 0.0, 0.0]

[10 rows x 3 columns]

from pervious section we know that how many times each word repeat now we apply a new function to all of query serches so we can obtain each word in query search belong to which catgory

In [ ]:
df_listed_name.head()

category_name  ...                                                dic
0                        آب انارگیری  ...  {'negin': 1, 'دستی': 8, 'اب': 10, 'انار': 9, '...
1  آب سردکن و تصفیه آب و لوازم جانبی  ...  {'تصفیه': 791, 'فیلتر': 478, 'اب': 805, 'سطلی'...
2                     آب مرکبات‌گیری  ...  {'tefal': 1, 'press': 62, 'مرکبات': 269, 'اب':...
3                           آب معدنی  ...  {'اب': 70, '6': 17, 'لیتری': 35, 'معدنی': 66, ...
4                 آباژور و چراغ خواب  ...  {'چراغ': 792, 'خواب': 760, 'نگهبان': 3, 'سگ': ...

[5 rows x 3 columns]

In [ ]:
lenght_df_listed_name = len(df_listed_name['list'])
def query_category (text):
  
  
  text = text.split(" ")
  le = len(text)
  cat = []
  cn=0   
  catee=''
  for j in text:
    #if j in "0987654321":
      #continue
    for i in range(lenght_df_listed_name):
      
      try:
        c = df_listed_name['dic'][i][j]
      except :
        c=0
      if c > cn :
        cn = c 
        catee = df_listed_name['category_name'][i]
    cat.append(catee)
  return cat


In [ ]:
df_listed_name.head(2)


category_name  ...                                                dic
0                        آب انارگیری  ...  {'negin': 1, 'وابمیوه': 1, 'دستی': 8, 'اب': 10...
1  آب سردکن و تصفیه آب و لوازم جانبی  ...  {'کوچک': 7, 'اب': 807, '928': 1, 'a': 19, 'فیل...

[2 rows x 3 columns]

In [ ]:
 df_listed_name['dic'][0]['negin']

1

In [ ]:
Er()
################################################################################ehra nashavad
lenght_df_listed_name = len(df_listed_name['list'])

def query_category2 (text , P):
  T = text.split(" ")
  cn = 0
  max_value = max(P) 
  max_index = number_list. index(max_value)
  cat = T[p]
  for i in range(lenght_df_listed_name):
      
      try:
        c = df_listed_name['dic'][i][cat]
      except :
        c=0
      cn = c 
      catee = df_listed_name['category_name'][i]
      print(catee)

In [ ]:
queries_test_offline_normalized.head(2)

0  ...                                                  3
0  تلویزیون 40 ایتچ  ...  [37.35209843269948, 31.819516639317843, 30.828...
1  قهوه ساز delongi  ...  [23.177961545819624, 24.218517755677862, 52.60...

[2 rows x 3 columns]

In [ ]:
queries_test_offline_normalized['4'] = queries_test_offline_normalized['2'].apply(query_category)

In [ ]:
queries_test_offline_normalized.head()

0  ...                                                  4
0    تلویزیون 40 ایتچ  ...  [سایر تلویزیون و لوازم جانبی, سایر تلویزیون و ...
1    قهوه ساز delongi  ...                                 [قهوه, قهوه, قهوه]
2  بند فلزی mi band 5  ...  [لوازم جانبی ساعت های معمولی و هوشمند, ماشین، ...
3       قالی زمردمشهد  ...                              [فرش, انگشتر, انگشتر]
4        پوکو x 3 pro  ...  [کیف و کاور گوشی و تبلت, کیف و کاور گوشی و تبل...

[5 rows x 4 columns]

In [ ]:
queries_test_offline_normalized.to_csv('queries_tfidf_finall2.csv')

In [ ]:
!cp queries_tfidf_finall2.csv  /content/drive/MyDrive/data_days

###now we use base algorithm

In [ ]:
searches_merged_train.head(2)

raw_query  ...                                       click_counts
0  گوشی موبایل  ...  [441, 369, 314, 286, 272, 245, 243, 229, 185, ...
1         گوشی  ...  [3184, 2749, 1819, 1727, 1709, 1485, 1336, 128...

[2 rows x 8 columns]

In [ ]:
base_products_normalized.head(2)

_id  ...                            product_name_normalized
0  yxwrs  ...  1920 x 1080 hd مدل سینمای ویدیو dlp اصلی video...
1  mbeby  ...  حجم کننده essence mascara ژل essence and masca...

[2 rows x 5 columns]

In [ ]:
base_products_normalized['sellers']  [0]

[{'availability': True,
  'date_added': '2018-06-10T17:27:45.418776+00:00',
  'name1': 'پروژکتور Optoma HD142X 1080p 3000 Lumens 3D DLP صفحه اصلی سینمای خانگی',
  'name2': 'Optoma HD142X 1080p 3000 Lumens 3D DLP Home Theater Projector',
  'price': 31852600},
 {'availability': False,
  'date_added': '2018-05-24T16:59:16.465159+00:00',
  'name1': 'ویدئو پروژکتور اوپتوما optoma hd142x : خانگی، 3D، رزولوشن 1920x1080 HD',
  'name2': '',
  'price': 12645000},
 {'availability': False,
  'date_added': '2019-02-17T00:49:49.573764+00:00',
  'name1': 'Video Projector Optoma HD142X',
  'name2': 'دیتا پروژکتور اپتما HD142X',
  'price': 12800000},
 {'availability': False,
  'date_added': '2019-09-24T19:29:08.728217+00:00',
  'name1': 'ویدئو پروژکتور اپتما OPTOMA HD142X',
  'name2': '',
  'price': 15900000},
 {'availability': False,
  'date_added': '2020-01-25T20:08:23.497684+00:00',
  'name1': 'پروژکتور اوپتوما مدل HD142X',
  'name2': '',
  'price': 12814000},
 {'availability': False,
  'date_added'

In [ ]:
base_products_normalized['sellers'][0][0]['price']

31852600

In [ ]:
price = []
_price= []
for feature in base_products_normalized['sellers'] :
  price.append(feature[0]['price'])
base_products_normalized['price'] = price

In [ ]:
date_added= []
for feature in base_products_normalized['sellers'] :
  date = feature[0]['date_added']
  date = date[0:date.find('.')]
  date_added.append(date)
base_products_normalized['date_added'] = date_added

In [ ]:
base_products_normalized.head(2)

_id           category_name  ...     price           date_added
0  yxwrs    ویدیو پروژکتور اپتما  ...  31852600  2018-06-10T17:27:45
1  mbeby  تقویت کننده مژه و ابرو  ...     60000  2020-06-29T20:02:26

[2 rows x 7 columns]

In [ ]:
from datetime import datetime

date_time_str = '2018-06-10T17:27:45'
#date_time_str = '18/09/19 01:55:19'

date_time_obj = datetime.strptime(date_time_str, '%Y-%m-%dT%H:%M:%S')
timestamp = datetime.timestamp(date_time_obj)

timestamp

1528651665.0

In [ ]:
def str_date (text) :
  #date = datetime.strptime(text, '%Y-%m-%dT%H:%M:%S')
  timestamp = datetime.timestamp(text)
  return timestamp

In [ ]:
base_products_normalized['date_added'] = base_products_normalized['date_added'].apply(str_date)

In [ ]:
base_products_normalized.head(2)

_id           category_name  ...     price    date_added
0  yxwrs    ویدیو پروژکتور اپتما  ...  31852600  1.528652e+09
1  mbeby  تقویت کننده مژه و ابرو  ...     60000  1.593461e+09

[2 rows x 7 columns]

In [ ]:
search_click_merge_2 = pd.read_csv('/content/drive/MyDrive/data_days/search_click_merge_2.csv')

In [ ]:
search_click_merge_2.drop(['Unnamed: 0'] , axis = 1 , inplace=True)

In [ ]:
searches_merged_train.head(2)

raw_query  ...                                       click_counts
0  گوشی موبایل  ...  [441, 369, 314, 286, 272, 245, 243, 229, 185, ...
1         گوشی  ...  [3184, 2749, 1819, 1727, 1709, 1485, 1336, 128...

[2 rows x 8 columns]

In [ ]:
search_click_merge_2.head()

raw_query_normalized  ...                                        cl_c_merged
0  0 خرید لوازم اشپزخونه اسباب بازی  ...  [('mmisn', 2), ('mmmze', 2), ('mrpgi', 2), ('m...
1                               088  ...  [('yqknb', 4), ('mkatq', 2), ('mkztd', 2), ('m...
2                    1 core samsung  ...  [('mmmkv', 4), ('upnlg', 2), ('mcpdi', 1), ('m...
3                            1 more  ...  [('maobx', 46), ('maajh', 25), ('magmg', 21), ...
4               1 more true stylish  ...         [('magmg', 4), ('yyirq', 4), ('mzawc', 2)]

[5 rows x 3 columns]

In [ ]:
type(search_click_merge_2.iloc[0,1])

str

In [ ]:
eval(search_click_merge_2.iloc[0,1])[0]

('mchww', 1)

In [ ]:
def str_lis(text) :
  return eval(text)
search_click_merge_2['r_c_merged'] = search_click_merge_2['r_c_merged'].apply(str_lis)
search_click_merge_2['cl_c_merged'] = search_click_merge_2['cl_c_merged'].apply(str_lis)

In [ ]:
search_click_merge_2.head()

raw_query_normalized  ...                                        cl_c_merged
0  0 خرید لوازم اشپزخونه اسباب بازی  ...  [(mmisn, 2), (mmmze, 2), (mrpgi, 2), (mylai, 2...
1                               088  ...   [(yqknb, 4), (mkatq, 2), (mkztd, 2), (mkatt, 1)]
2                    1 core samsung  ...  [(mmmkv, 4), (upnlg, 2), (mcpdi, 1), (mmmzn, 1...
3                            1 more  ...  [(maobx, 46), (maajh, 25), (magmg, 21), (magmu...
4               1 more true stylish  ...               [(magmg, 4), (yyirq, 4), (mzawc, 2)]

[5 rows x 3 columns]

In [ ]:
search_click_merge_2[search_click_merge_2['raw_query_normalized'] =='گوشی موبایل' ]

raw_query_normalized  ...                                        cl_c_merged
84261          گوشی موبایل  ...  [('mmmbf', 443), ('mmmbn', 374), ('mmmbg', 315...

[1 rows x 3 columns]

In [ ]:
search_click_merge_2.iloc[0,1][0][0]

'mchww'

In [ ]:
base_products_normalized.head(2)

_id           category_name  ...     price    date_added
0  yxwrs    ویدیو پروژکتور اپتما  ...  31852600  1.528652e+09
1  mbeby  تقویت کننده مژه و ابرو  ...     60000  1.593461e+09

[2 rows x 7 columns]

In [ ]:
base_products_normalized['product_name_normalized'] = base_products_normalized['product_name_normalized'].apply(eli_dup)
base_products_normalized['product_name'] = base_products_normalized['product_name'].apply(eli_dup)

In [ ]:
base_products_normalized.to_csv("base_products_normalized_finall.csv")
!cp base_products_normalized_finall.csv /content/drive/MyDrive/data_days

In [ ]:
base_products_normalized.head()

_id           category_name  ...     price    date_added
0  yxwrs    ویدیو پروژکتور اپتما  ...  31852600  1.528652e+09
1  mbeby  تقویت کننده مژه و ابرو  ...     60000  1.593461e+09
2  yovgc             مام و اسپری  ...         0  1.588267e+09
3  yokff             مام و اسپری  ...     49000  1.586876e+09
4  uduyq              گوشی هوآوی  ...         0  1.493062e+09

[5 rows x 7 columns]

In [ ]:
search_click_merge_2['tf_idf_priority'] = search_click_merge_2['raw_query_normalized'].apply(tfidf_priority)

In [ ]:
def x100 (L):
  sum = 0 
  for i in L:
    sum+=i
  
  a = [element *100/sum for element in L]
  return a

In [ ]:
search_click_merge_2['tf_idf_priority'] = search_click_merge_2['tf_idf_priority'].apply(x100)

In [ ]:
search_click_merge_2.head(3)

raw_query_normalized  ...                                    tf_idf_priority
0  0 خرید لوازم اشپزخونه اسباب بازی  ...  [0.0, 0.0, 22.89784759305035, 38.6704375708426...
1                               088  ...                                            [100.0]
2                    1 core samsung  ...        [0.0, 56.93819411118658, 43.06180588881341]

[3 rows x 4 columns]

In [ ]:
search_click_merge_2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 86535 entries, 0 to 86534
Data columns (total 5 columns):
 #   Column                Non-Null Count  Dtype 
---  ------                --------------  ----- 
 0   raw_query_normalized  86535 non-null  object
 1   r_c_merged            86535 non-null  object
 2   cl_c_merged           86535 non-null  object
 3   tf_idf_priority       86535 non-null  object
 4   tf-idf_priority       86535 non-null  object
dtypes: object(5)
memory usage: 3.3+ MB


In [ ]:
search_click_merge_2.to_csv('search_click_merge_2_finall2.csv')
!cp search_click_merge_2_finall2.csv /content/drive/MyDrive/data_days

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
search_click_merge_2 = pd.read_csv('/content/drive/MyDrive/data_days/search_click_merge_2_finall2.csv')
search_click_merge_2.drop(['Unnamed: 0'] , axis = 1 , inplace = True)

In [ ]:
search_click_merge_2.head(2)

raw_query_normalized  ...                                    tf-idf_priority
0  0 خرید لوازم اشپزخونه اسباب بازی  ...  [0.0, 0.0, 22.89784759305035, 38.6704375708426...
1                               088  ...                                            [100.0]

[2 rows x 5 columns]

In [ ]:
def str_lis(text) :
  return eval(text)
search_click_merge_2['r_c_merged'] = search_click_merge_2['r_c_merged'].apply(str_lis)
search_click_merge_2['cl_c_merged'] = search_click_merge_2['cl_c_merged'].apply(str_lis)
search_click_merge_2['tf_idf_priority'] = search_click_merge_2['tf_idf_priority'].apply(str_lis)


In [ ]:
base_products_normalized = pd.read_csv('/content/drive/MyDrive/data_days/base_products_normalized_finall.csv')
base_products_normalized.drop(['Unnamed: 0'] , axis = 1 , inplace = True)

In [ ]:
base_products_normalized.head(2)

_id           category_name  ...     price    date_added
0  yxwrs    ویدیو پروژکتور اپتما  ...  31852600  1.528652e+09
1  mbeby  تقویت کننده مژه و ابرو  ...     60000  1.593461e+09

[2 rows x 7 columns]

In [ ]:
base_products_normalized.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1769291 entries, 0 to 1769290
Data columns (total 7 columns):
 #   Column                   Dtype  
---  ------                   -----  
 0   _id                      object 
 1   category_name            object 
 2   sellers                  object 
 3   product_name             object 
 4   product_name_normalized  object 
 5   price                    int64  
 6   date_added               float64
dtypes: float64(1), int64(1), object(5)
memory usage: 94.5+ MB


In [ ]:
base_products_normalized[base_products_normalized['_id'] == 'mchww'].iloc[0,5]

193000

In [ ]:
search_click_merge_2.iloc[0]['raw_query_normalized']

'0 خرید لوازم اشپزخونه اسباب بازی'

In [ ]:
search_click_merge_2.iloc[247:249]

raw_query_normalized  ...                         tf-idf_priority
247                  5 3  ...  [56.52173913043479, 43.47826086956522]
248                  5 g  ...  [56.52173913043479, 43.47826086956522]

[2 rows x 5 columns]

In [ ]:
base_products_normalized.head()

_id           category_name  ...     price    date_added
0  yxwrs    ویدیو پروژکتور اپتما  ...  31852600  1.528652e+09
1  mbeby  تقویت کننده مژه و ابرو  ...     60000  1.593461e+09
2  yovgc             مام و اسپری  ...         0  1.588267e+09
3  yokff             مام و اسپری  ...     49000  1.586876e+09
4  uduyq              گوشی هوآوی  ...         0  1.493062e+09

[5 rows x 7 columns]

In [ ]:
lengh

86535

In [ ]:
lengh = len(search_click_merge_2['raw_query_normalized'])
#lengh = 10
sample =2
df = {"raw_query_normalized":[],"product_name":[] ,"product_id":[] ,"Conformity":[],"number":[] ,"price":[] ,"time_added":[] };
for row_c in tqdm(range(lengh)):
  
  row = search_click_merge_2.iloc[row_c]
  c=-1
  for product_c in range(len(row['cl_c_merged'])) :
    c+=1
    product = row['cl_c_merged'][c]
    tf_idf = row['tf_idf_priority']

    if c == sample :
      break 
    k = base_products_normalized[base_products_normalized['_id'] ==product[0] ]
    
    
    df['product_id'].append(product[0])
    query = row['raw_query_normalized']
    df["raw_query_normalized"].append(query)
    df['number'].append(product[1])
    p = k.iloc[0,5]
    df['price'].append(p)
    D = k.iloc[0,6]
    df['time_added'].append(D)
    product_name =  k.iloc[0,4]
    df["product_name"].append(product_name)
    #if row['tf-idf_priority'] ==[]:
    #  row['tf-idf_priority'] = [100]
    per = list_text_comp(product_name ,query,tf_idf )
    df["Conformity"].append(per)



 66%|██████▌   | 56941/86535 [3:09:37<1:44:59,  4.70it/s]

In [ ]:
df_2 = pd.DataFrame.from_dict(df )  

In [ ]:
df_2.to_csv("train_data2.csv")
!cp train_data2.csv /content/drive/MyDrive/data_days

In [ ]:
df.to_csv("train_data.csv")
!cp train_data.csv /content/drive/MyDrive/data_days

In [ ]:
df.head()

raw_query_normalized  ...    time_added
0  0 خرید لوازم اشپزخونه اسباب بازی  ...  1.616528e+09
1                               088  ...  1.600753e+09
2                    1 core samsung  ...  1.607188e+09
3                            1 more  ...  1.618845e+09
4               1 more true stylish  ...  1.607842e+09

[5 rows x 7 columns]

In [ ]:
search_click_merge_2.head(2)

raw_query_normalized  ...                         tf_idf_priority_normalized
0  0 خرید لوازم اشپزخونه اسباب بازی  ...  [0.0, 0.0, 0.2289784759305035, 0.3867043757084...
1                               088  ...                                              [1.0]

[2 rows x 6 columns]

In [ ]:
def strr ( text):
  return str(text)

df['raw_query_normalized'] = df['raw_query_normalized'].apply(strr)

In [ ]:
df

raw_query_normalized  ...    time_added
0      0 خرید لوازم اشپزخونه اسباب بازی  ...  1.616528e+09
1                                   088  ...  1.600753e+09
2                        1 core samsung  ...  1.607188e+09
3                                1 more  ...  1.618845e+09
4                   1 more true stylish  ...  1.607842e+09
...                                 ...  ...           ...
86530                      ییخچال فریزر  ...  1.611223e+09
86531                  ییخچال فریزر دوو  ...  1.585521e+09
86532                             ییسیم  ...  1.534679e+09
86533                           ییونتوس  ...  1.570265e+09
86534                         ییکس باکس  ...  1.592169e+09

[86535 rows x 7 columns]

In [ ]:
df.to_csv("train_data.csv")
!cp train_data.csv /content/drive/MyDrive/data_days

In [ ]:
  df = pd.DataFrame.from_dict(df)  
df.head()

raw_query_normalized  ...    time_added
0  0 خرید لوازم اشپزخونه اسباب بازی  ...  1.616528e+09
1  0 خرید لوازم اشپزخونه اسباب بازی  ...  1.613644e+09
2                               088  ...  1.600753e+09
3                               088  ...  1.616204e+09
4                    1 core samsung  ...  1.607188e+09

[5 rows x 7 columns]

In [ ]:
df[20:25]

raw_query_normalized  ...    time_added
20                  10 دلار  ...  1.610611e+09
21                   10 پرو  ...  1.609981e+09
22                 1000 تست  ...  1.618071e+09
23  1000 تست استعداد تحلیلی  ...  1.618071e+09
24          1000 تست تحلیلی  ...  1.618071e+09

[5 rows x 7 columns]

In [ ]:
search_click_merge_2[20:25]

raw_query_normalized  ...                                    tf-idf_priority
20                  10 دلار  ...              [34.33667065030409, 65.6633293496959]
21                   10 پرو  ...            [41.00474636379352, 58.995253636206485]
22                 1000 تست  ...             [44.36691176061316, 55.63308823938683]
23  1000 تست استعداد تحلیلی  ...  [17.966344469908762, 22.528573379790274, 29.98...
24          1000 تست تحلیلی  ...  [25.661279469676185, 32.17749823956488, 42.161...

[5 rows x 5 columns]

In [ ]:
def x100 (L):
  sum = 0 
  for i in L:
    sum+=i
  
  a = [element *1/sum for element in L]
  return a
search_click_merge_2['tf_idf_priority_normalized'] = search_click_merge_2['tf_idf_priority'].apply(x100)

In [ ]:
search_click_merge_2.head()

raw_query_normalized  ...                         tf_idf_priority_normalized
0  0 خرید لوازم اشپزخونه اسباب بازی  ...  [0.0, 0.0, 0.2289784759305035, 0.3867043757084...
1                               088  ...                                              [1.0]
2                    1 core samsung  ...      [0.0, 0.5693819411118659, 0.4306180588881341]
3                            1 more  ...                                         [0.0, 1.0]
4               1 more true stylish  ...  [0.0, 0.31912718919683797, 0.3143489324367585,...

[5 rows x 6 columns]

In [ ]:
#this block used for return a score that obtain similarity of product_name and query search

def list_text_comp(product_name , text , priority):
  Conformity_percentage = 0
  counter_Conformity = -1 
  #text = correction (text)
  #text = _normalize_text(text )
  #print(text)
  P_text=priority
  text_splited = text.split(" ")
  product_name_splited = product_name.split(" ")

  for counter_text in text_splited:
    counter_Conformity+=1
    for counter_product in product_name_splited:
      if counter_product == counter_text:
        Conformity_percentage += P_text[counter_Conformity]
 
  return Conformity_percentage
  
  

In [ ]:
def finall4(text , priority , list_df) :
  try :
    list_df = set(list_df)
    list_df = list(list_df)
    len_df=len(list_df)
    dff = []
    for i in range(len_df):
      k = base_products_normalized[base_products_normalized['category_name'] == list_df[i]].copy()
      dff.append(k)

    dff = pd.concat(dff)
    dff.reset_index(inplace=True)
    base_products_normalized_lenght = len(dff["product_name_normalized"])
    P = max(priority)

    j =0
    counter = 0
    d=0
    c = 0 
    k = 0
    top10 = {"ID":[],"click":[],"Conformity":[]};

    for i in range(base_products_normalized_lenght):
      counter = list_text_comp(dff["product_name_normalized"][i] , text ,priority)
      

In [ ]:

def finall3(text , priority,list_df):
  try :
    list_df = set(list_df)
    list_df = list(list_df)
    len_df=len(list_df)
    dff = []
    for i in range(len_df):
      k = base_products_normalized[base_products_normalized['category_name'] == list_df[i]].copy()
      dff.append(k)

    dff = pd.concat(dff)
    dff.reset_index(inplace=True)
    base_products_normalized_lenght = len(dff["product_name_normalized"])
    if len_df == 1:
      P = priority[0]  
    else:
      P = priority[1]                        #priority[0] fo faster answer
    
    #df = pd.DataFrame(data = None, columns=[0 , 1 ,2 ])
    j =0
    counter = 0
    d=0
    c = 0 
    k = 0
    top10 = {"ID":[],"click":[],"Conformity":[]};
    
    for i in range(base_products_normalized_lenght):
      counter = list_text_comp(dff["product_name_normalized"][i] , text ,priority)
      if counter >= P:
        Id = dff["_id"][i]
        #print(counter)
        try:
          
          top10["ID"].append(Id)
          top10["click"].append(dff["click_number"][i])
          top10["Conformity"].append(counter)
          """  
            c+=1
            if counter ==100:
              d+=1
              
            if counter > 60:
              k+=1
            
            
            if   d>=6 or k>=10 :
              df = pd.DataFrame.from_dict(top10)  
              df.sort_values(by=["Conformity", "click"] ,ascending=False, inplace=True)
              return df 
          """  
        except:
          pass
  except:
    top10 = {"ID":[],"click":[],"Conformity":[]};
    top10["ID"].append('mmmmm')
    top10["click"].append(0)
    top10["Conformity"].append(0)
    print(text)
      
  df = pd.DataFrame.from_dict(top10)  
  df.sort_values(by=["Conformity" , "click"] ,ascending=False, inplace=True)
  return df
  

  

test

In [ ]:
text = "aspire 7"
list_df = queries_test_offline_normalized[queries_test_offline_normalized['2'] == text].iloc[0,3]
list_df

['قطعات داخلی لپ\u200cتاپ ایسر']

In [ ]:
finall3(text , priority(text),list_df)

ID  click  Conformity
9    kgtyp      1  100.000000
11   kgtyl      1  100.000000
93   kkxoi      0  100.000000
94   kkxig      0  100.000000
103  kjbsb      0  100.000000
..     ...    ...         ...
384  kffut      0   56.521739
385  kffuk      0   56.521739
386  mcpwq      0   56.521739
387  kffua      0   56.521739
388  kwdcx      0   56.521739

[389 rows x 3 columns]

In [ ]:
base_products_normalized[base_products_normalized['_id'] == 'mmmmm']

_id  ... click_number
5563  mmmmm  ...         1458

[1 rows x 6 columns]

In [ ]:
queries_test_offline_normalized.head(2)

0  ...                                                  4
0  تلویزیون 40 ایتچ  ...  [سایر تلویزیون و لوازم جانبی, سایر تلویزیون و ...
1  قهوه ساز delongi  ...                                 [قهوه, قهوه, قهوه]

[2 rows x 4 columns]

In [ ]:
def finall4() :
  df = pd.DataFrame(data = None, columns=[0,1,2,3,4,5,6,7,8,9 ])
  j=0
  for i in tqdm(queries_test_offline_normalized['2']):
    #if j == 30:
      #return df
    data = list(finall3(i ,queries_test_offline_normalized['3'][j],queries_test_offline_normalized['4'][j] )[0:10]["ID"])
    df = df.append([data],ignore_index=True )
    j+=1
  return df

In [ ]:
queries_test_offline_normalized.iloc[17]

0                                  aspire 7
2                                  aspire 7
3    [56.52173913043479, 43.47826086956522]
4                 [قطعات داخلی لپ‌تاپ ایسر]
Name: 17, dtype: object

In [ ]:
result = finall4()

  2%|▏         | 629/38724 [06:33<10:06:10,  1.05it/s]

  2%|▏         | 725/38724 [07:32<3:26:46,  3.06it/s]

8


  7%|▋         | 2607/38724 [26:00<5:07:56,  1.95it/s]

 10%|█         | 3899/38724 [38:44<3:12:55,  3.01it/s]

...

 96%|█████████▌| 37231/38724 [6:11:17<07:55,  3.14it/s]

21
21


 99%|█████████▉| 38240/38724 [6:21:23<07:29,  1.08it/s]

5 4
5 4


100%|██████████| 38724/38724 [6:25:51<00:00,  1.67it/s]



In [ ]:
result.head()

0      1      2      3      4      5      6      7      8      9
0  mymqh  mgswy  mgswa  mgswb  mpiki  morhq  moetg  morhc  ylzgf  mjovc
1  mybod  myzov  mbfvx  mzghk  mbfvo  mdtxh  mdtsm  mzxuw  mwiat  mzghb
2  mkami  mkamo  mkamw  mlabv  mkhiy  mkamr  mkwxt  bmznr  mvbeh  mtcbn
3  unifg  ungic  mwpeu  mpaaq  mifgj  mosir  mwyth  mjlrz  ynlsf  ucrtw
4  mmiqz  mmipl  mibnd  mmnet  mktqn  mkdov  mnkeh  mnyzb  mkdol  mmobw

0      1      2      3      4      5      6      7      8      9
0  mymqh  mgswy  mgswa  mgswb  mpiki  morhq  moetg  morhc  ylzgf  mjovc
1  mybod  myzov  mbfvx  mzghk  mbfvo  mdtxh  mdtsm  mzxuw  mwiat  mzghb
2  mkami  mkamo  mkamw  mlabv  mkhiy  mkamr  mkwxt  bmznr  mvbeh  mtcbn
3  unifg  ungic  mwpeu  mpaaq  mifgj  mosir  mwyth  mjlrz  ynlsf  ucrtw
4  mmiqz  mmipl  mibnd  mmnet  mktqn  mkdov  mnkeh  mnyzb  mkdol  mmobw

In [ ]:
def read_lowmem(path):
  with open(path) as f:
    res = [json.loads(line) for line in tqdm(f)]
    res = pd.DataFrame(res)
  return res
queries_test_offline = read_lowmem("/content/data/queries_test_offline.json")
queries_test_offline.head()

38724it [00:00, 214363.79it/s]


0
0    تلویزیون 40 ایتچ
1     قهوه سازDelongi
2  بند فلزی mi band 5
3       قالی زمردمشهد
4          پوکوx3 pro

In [ ]:
result = pd.concat([queries_test_offline[0], result], axis=1)

In [ ]:
result.head()

In [ ]:
result2 = result.copy()
result2 = result2.fillna('mmmmm')

In [ ]:
result2 = result2.fillna('mmmmm')

In [ ]:
result2

In [ ]:
result2.iloc[38691]

In [ ]:

#result.fillna('mmmmm')
result2.to_csv('result.csv' ,index=False ,header =False )
!cp result.csv /content/drive/MyDrive/re

In [ ]:

#result.fillna('mmmmm')
#result.to_csv('result1.csv' ,index=False , header =False)
#!cp queries.csv /content/drive/MyDrive

In [ ]:
!pip install git+https://github.com/RoboEpics/roboepics-client.git@d50db61a92ab14f5e95c87679b681a0836a3f6e5
from roboepics_client.roboepics_client import RoboEpicsClient

problem_id = 4  # This value is set according to your user. Do not change it please.
problem_enter_id = 189  # This value is set according to your user. Do not change it please.
roboepics_client = RoboEpicsClient(problem_id, problem_enter_id)

  Cloning https://github.com/RoboEpics/roboepics-client.git (to revision d50db61a92ab14f5e95c87679b681a0836a3f6e5) to /tmp/pip-req-build-rm_jn7iu
  Running command git clone -q https://github.com/RoboEpics/roboepics-client.git /tmp/pip-req-build-rm_jn7iu
  Running command git rev-parse -q --verify 'sha^d50db61a92ab14f5e95c87679b681a0836a3f6e5'
  Running command git fetch -q https://github.com/RoboEpics/roboepics-client.git d50db61a92ab14f5e95c87679b681a0836a3f6e5
Open this URL and confirm your login: https://fusion.roboepics.com/oauth2/device?client_id=7126a051-baea-4fe1-bdf8-fde2fdb31f97&user_code=PV6P7K
Login successful.


In [ ]:
roboepics_client.submit("/content/drive/MyDrive/result.csv")

In [ ]:
!cp result.csv /content/drive/MyDrive/re/results

In [ ]:
example1 = "/content/drive/MyDrive/re/results"


In [ ]:
with open(example1, "r") as file1:
    print(file1.read(10000))

In [ ]:
#برای کلماتی که تعداد کمی برگزیده پیدا می کنند میتوان بقیه آن را با بیشترین کلیک در اون کتگوری انتخاب کرد

In [ ]:
#اهمیت تعداد کلیک بالا ها در کتگوری